In [1]:
import tensorflow as tf
import numpy as np
from glob import glob
import matplotlib.pyplot as plt

#from tensorflow_examples.models.pix2pix import pix2pix
from IPython.display import clear_output

In [2]:
PATH = "data"
PREDICTION_SAVE_PATH = "predictions"
AUTOTUNE = tf.data.experimental.AUTOTUNE
WIDTH, HEIGHT = 512, 512
BATCH_SIZE = 4

In [3]:
def load_data(path):
    images = sorted(glob(f"{path}/images/*.png"))
    masks = sorted(glob(f"{path}/masks/*.png"))
    return images, masks

image_files, mask_files = load_data(PATH)

In [4]:
print(len(image_files), len(mask_files))
DATASET_SIZE = len(image_files)

2667 2667


In [5]:
dataset = tf.data.Dataset.from_tensor_slices((image_files, mask_files))

In [6]:
def normalize(input_image, input_mask):
    input_image = tf.cast(input_image, tf.float32)/ 255.0
    #input_mask = tf.cast(input_mask, tf.uint8)
    input_mask = tf.cast(input_mask, tf.float32)/ 255.0
    #input_mask -= 1
    
    return input_image, input_mask


def parse_image(image_file, mask_file):
    #print(image_file, mask_file)
    img = tf.io.read_file(image_file)
    img = tf.image.decode_png(img, channels=3)
    img = tf.image.resize(img, size=(WIDTH, HEIGHT))
    msk = tf.io.read_file(mask_file)
    msk = tf.image.decode_png(msk, channels=3)
    msk = tf.image.resize(msk, size=(WIDTH, HEIGHT))
    
    img, msk = normalize(img, msk)
    
    return img, msk

In [7]:
dataset = dataset.map(parse_image).batch(BATCH_SIZE)
dataset = dataset.prefetch(buffer_size=AUTOTUNE)

In [8]:
def display(display_list):
    plt.figure(figsize=(WIDTH, HEIGHT))
    print(display_list)
    title = ['input image', 'true mask', 'predicted mask']
    
    for i in range(len(display_list)):
        plt.subplot(1, len(display_list), i+1)
        plt.title(title[i])
        plt.imshow(tf.keras.preprocessing.image.array_to_img(display_list[i]))
        plt.axis('off')
    plt.show()
    
for image, mask in dataset.take(2):
    sample_image, sample_mask = image, mask
    
display([sample_image[1], sample_mask[1]])

[<tf.Tensor: shape=(512, 512, 3), dtype=float32, numpy=
array([[[0.7882353 , 0.78431374, 0.7764706 ],
        [0.7882353 , 0.78431374, 0.7764706 ],
        [0.7873517 , 0.78343016, 0.775587  ],
        ...,
        [0.8509804 , 0.84313726, 0.84705883],
        [0.8509804 , 0.84313726, 0.84705883],
        [0.8509804 , 0.84313726, 0.84705883]],

       [[0.79154414, 0.7876226 , 0.77977943],
        [0.79154414, 0.7876226 , 0.77977943],
        [0.79154414, 0.7876226 , 0.77977943],
        ...,
        [0.8509804 , 0.84313726, 0.84705883],
        [0.8509804 , 0.84313726, 0.84705883],
        [0.8509804 , 0.84313726, 0.84705883]],

       [[0.8       , 0.79607844, 0.7882353 ],
        [0.8       , 0.79607844, 0.7882353 ],
        [0.80036384, 0.7964423 , 0.78859913],
        ...,
        [0.8509804 , 0.84313726, 0.84705883],
        [0.8509804 , 0.84313726, 0.84705883],
        [0.8509804 , 0.84313726, 0.84705883]],

       ...,

       [[0.11103863, 0.10711706, 0.09927392],
        [0.1

In [9]:
print(dataset)

<PrefetchDataset shapes: ((None, 512, 512, 3), (None, 512, 512, 3)), types: (tf.float32, tf.float32)>


In [10]:
from tensorflow.keras import backend as K
from tensorflow.keras.layers import Activation, Lambda, GlobalAveragePooling2D, concatenate
from tensorflow.keras.layers import UpSampling2D, Conv2D, Dropout, MaxPooling2D, Conv2DTranspose
from tensorflow.keras.layers import Dense, Flatten, Input
from tensorflow.keras.models import Model, Sequential, load_model
from tensorflow.keras.callbacks import ModelCheckpoint, ReduceLROnPlateau

In [11]:
def get_model():
    in1 = tf.keras.layers.Input(shape=(HEIGHT, WIDTH, 3 ))

    conv1 = Conv2D(32, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(in1)
    conv1 = Dropout(0.2)(conv1)
    conv1 = Conv2D(32, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(conv1)
    pool1 = MaxPooling2D((2, 2))(conv1)

    conv2 = Conv2D(64, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(pool1)
    conv2 = Dropout(0.2)(conv2)
    conv2 = Conv2D(64, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(conv2)
    pool2 = MaxPooling2D((2, 2))(conv2)

    conv3 = Conv2D(128, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(pool2)
    conv3 = Dropout(0.2)(conv3)
    conv3 = Conv2D(128, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(conv3)
    pool3 = MaxPooling2D((2, 2))(conv3)

    conv4 = Conv2D(128, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(pool3)
    conv4 = Dropout(0.2)(conv4)
    conv4 = Conv2D(128, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(conv4)

    up1 = concatenate([UpSampling2D((2, 2))(conv4), conv3], axis=-1)
    conv5 = Conv2D(64, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(up1)
    conv5 = Dropout(0.2)(conv5)
    conv5 = Conv2D(64, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(conv5)
    
    up2 = concatenate([UpSampling2D((2, 2))(conv5), conv2], axis=-1)
    conv6 = Conv2D(64, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(up2)
    conv6 = Dropout(0.2)(conv6)
    conv6 = Conv2D(64, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(conv6)

    up2 = concatenate([UpSampling2D((2, 2))(conv6), conv1], axis=-1)
    conv7 = Conv2D(32, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(up2)
    conv7 = Dropout(0.2)(conv7)
    conv7 = Conv2D(32, (3, 3), activation='relu', kernel_initializer='he_normal', padding='same')(conv7)
    segmentation = Conv2D(3, (1, 1), activation='sigmoid', name='seg')(conv7)

    model = Model(inputs=[in1], outputs=[segmentation])

    losses = {'seg': 'binary_crossentropy'
            }

    metrics = {'seg': ['acc']
                }
    model.compile(optimizer="adam", loss = losses, metrics=metrics)

    return model

In [12]:
model = get_model()
model.summary()

Model: "model"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_1 (InputLayer)            [(None, 512, 512, 3) 0                                            
__________________________________________________________________________________________________
conv2d (Conv2D)                 (None, 512, 512, 32) 896         input_1[0][0]                    
__________________________________________________________________________________________________
dropout (Dropout)               (None, 512, 512, 32) 0           conv2d[0][0]                     
__________________________________________________________________________________________________
conv2d_1 (Conv2D)               (None, 512, 512, 32) 9248        dropout[0][0]                    
______________________________________________________________________________________________

In [13]:
def save_prediction(predicted, epoch):
    pred_img = tf.keras.preprocessing.image.array_to_img(predicted)
    pred_img.save(f"{PREDICTION_SAVE_PATH}/epoch-{epoch}.png")

def create_mask(pred_mask):
  pred_mask = tf.argmax(pred_mask, axis=-1)
  pred_mask = pred_mask[..., tf.newaxis]
  return pred_mask[0]

def show_predictions(dataset=None, num=2, is_save=False, epoch=0):
  if dataset:
    for image, mask in dataset.take(num):
      pred_mask = model.predict(image)
      created_mask = create_mask(pred_mask)
      display([image[0], mask[0], created_mask])
      if is_save:
        save_prediction(created_mask, epoch)
  else:
    display([sample_image, sample_mask,
             create_mask(model.predict(sample_image[tf.newaxis, ...]))])
    
show_predictions(dataset, 2, True) 

[<tf.Tensor: shape=(512, 512, 3), dtype=float32, numpy=
array([[[2.02205889e-02, 9.69362780e-02, 2.68326819e-01],
        [2.35294122e-02, 9.80219841e-02, 2.66578585e-01],
        [2.35294122e-02, 9.80392173e-02, 2.64154404e-01],
        ...,
        [0.00000000e+00, 2.14276955e-01, 4.38112736e-01],
        [1.14698219e-03, 2.16894537e-01, 4.33421403e-01],
        [2.25566793e-03, 2.18665749e-01, 4.40730304e-01]],

       [[2.16911770e-02, 9.74264741e-02, 2.67017066e-01],
        [2.01171879e-02, 9.14636925e-02, 2.69975483e-01],
        [2.35294122e-02, 9.80392173e-02, 2.62965292e-01],
        ...,
        [1.18910847e-03, 2.19033390e-01, 4.33873326e-01],
        [6.64445455e-04, 2.13206574e-01, 4.26200598e-01],
        [2.01056988e-04, 2.17375159e-01, 4.40090775e-01]],

       [[2.29817703e-02, 9.80392173e-02, 2.65379906e-01],
        [2.34202668e-02, 9.80028361e-02, 2.65062034e-01],
        [2.07912065e-02, 9.54254717e-02, 2.65931368e-01],
        ...,
        [4.36963839e-03, 2.2062

[<tf.Tensor: shape=(512, 512, 3), dtype=float32, numpy=
array([[[0.2454506 , 0.20623492, 0.16645986],
        [0.2861802 , 0.24622995, 0.20701426],
        [0.14804639, 0.10883071, 0.07353659],
        ...,
        [0.11776123, 0.15697692, 0.11383966],
        [0.11990248, 0.15127504, 0.10029464],
        [0.10611884, 0.13749139, 0.08651099]],

       [[0.23559427, 0.19637857, 0.15702647],
        [0.3505572 , 0.3076246 , 0.26840892],
        [0.27392483, 0.23470914, 0.1975732 ],
        ...,
        [0.1015412 , 0.14075689, 0.09761963],
        [0.12336665, 0.1547392 , 0.1037588 ],
        [0.12740982, 0.16172282, 0.10780197]],

       [[0.18405953, 0.13100992, 0.09752581],
        [0.27878895, 0.22780858, 0.19251446],
        [0.26870307, 0.2177227 , 0.18242858],
        ...,
        [0.10064697, 0.13986266, 0.0967254 ],
        [0.1102405 , 0.14161305, 0.09063266],
        [0.09537162, 0.12674417, 0.07576378]],

       ...,

       [[0.18177682, 0.18595761, 0.16216898],
        [0.1

In [14]:
train_size = int(0.8 * DATASET_SIZE)
val_size = int(0.1 * DATASET_SIZE)
test_size = int(0.1 * DATASET_SIZE)

print(train_size, val_size, test_size)

train_ds = dataset.take(train_size)
test_ds = dataset.skip(train_size)
validation_ds = test_ds.skip(test_size)
test_ds = test_ds.take(test_size)

print(train_ds, test_ds, validation_ds)

2133 266 266
<TakeDataset shapes: ((None, 512, 512, 3), (None, 512, 512, 3)), types: (tf.float32, tf.float32)> <TakeDataset shapes: ((None, 512, 512, 3), (None, 512, 512, 3)), types: (tf.float32, tf.float32)> <SkipDataset shapes: ((None, 512, 512, 3), (None, 512, 512, 3)), types: (tf.float32, tf.float32)>


In [15]:
class DisplayCallback(tf.keras.callbacks.Callback):
  def on_epoch_end(self, epoch, logs=None):
    clear_output(wait=True)
    epoch_num = epoch+1
    show_predictions(dataset, 2, True, epoch_num)
    print ('\nSample Prediction after epoch {}\n'.format(epoch_num))

In [16]:
print(train_ds)
print(test_ds)

<TakeDataset shapes: ((None, 512, 512, 3), (None, 512, 512, 3)), types: (tf.float32, tf.float32)>
<TakeDataset shapes: ((None, 512, 512, 3), (None, 512, 512, 3)), types: (tf.float32, tf.float32)>


In [17]:
print(model.input)
print(model.output)

KerasTensor(type_spec=TensorSpec(shape=(None, 512, 512, 3), dtype=tf.float32, name='input_1'), name='input_1', description="created by layer 'input_1'")
KerasTensor(type_spec=TensorSpec(shape=(None, 512, 512, 3), dtype=tf.float32, name=None), name='seg/Sigmoid:0', description="created by layer 'seg'")


In [ ]:
EPOCHS = 1
VAL_SUBSPLITS = 5
VALIDATION_STEPS = test_size//BATCH_SIZE//VAL_SUBSPLITS
STEPS_PER_EPOCH = train_size//BATCH_SIZE

#model_history = model.fit(train_ds, epochs=EPOCHS,
#                          steps_per_epoch=STEPS_PER_EPOCH,
#                          validation_steps=VALIDATION_STEPS,
#                          validation_data=test_ds,
#                          callbacks=[DisplayCallback()])

model_history = model.fit(train_ds, epochs=EPOCHS,
                          validation_data=test_ds,
                          callbacks=[DisplayCallback()])

494/667 [=====================>........] - ETA: 4:01 - loss: 0.5877 - acc: 0.2908